In [1]:
'''
FIRST OBTAIN CHARACTER EMBEDDINGS USING BIDIRECTIONAL LSTM

THEN, CONCAT THE CHARACTER EMBEDDINGS TO OBTAIN WORD EMBEDDINGS

PASS THIS THROUGH A BiLSTM ENCODER

THEN CONCAT THE EMBEDDINGS: Vobt + Vpre_trained = Vword

PASS THESE Vword through an LSTM and then through a softmax function for performing NER

'''

'\nFIRST OBTAIN CHARACTER EMBEDDINGS USING BIDIRECTIONAL LSTM\n\nTHEN, CONCAT THE CHARACTER EMBEDDINGS TO OBTAIN WORD EMBEDDINGS\n\nPASS THIS THROUGH A BiLSTM ENCODER\n\nTHEN CONCAT THE EMBEDDINGS: Vobt + Vpre_trained = Vword\n\nPASS THESE Vword through an LSTM and then through a softmax function for performing NER\n\n'

In [2]:
import re

def split_into_sentences(text):
    sentences = re.split(r'(?<!\w\.\w.)(?<![A-Z][a-z]\.)(?<=\.|\?)\s', text)
    return sentences

# Example usage:
text = "This is a sentence. And this is another sentence? Finally, this is the last sentence."
sentences = split_into_sentences(text)
print(sentences)


['This is a sentence.', 'And this is another sentence?', 'Finally, this is the last sentence.']


In [3]:
from datasets import load_dataset

dataset = load_dataset("zhengyun21/PMC-Patients")

l = []
for i in range(len(dataset['train'])):
    if ('brain' in dataset['train'][i]['patient'] and 'MRI' in dataset['train'][i]['patient']):
        l.append(i)

#TO EXTRACT HISTORY OF THE FIRST PATIENT IN THE LIST, USE:
dataset['train'][11]

osl = []
for i in range(1800):
    osl.append(dataset['train'][l[i]]['patient'])

# piped_out = []
# for j in range(50):
#     original_string = osl[j]
#     piped_out.append(pipe(original_string))

# osl[2]

#LET US OBTAIN DATA ONLY UPTO MRI
l = []
for i in range(len(osl)):
    t = split_into_sentences(osl[i])
    s = ""
    for j in range(len(t)):
        s += t[j]
        if 'MRI' in t[j]:
            break
    l.append(s)
 
    osl[i] = s
    
#OSL IS THE ACTUAL DATA INSIDE THE LIST

/home/rvcse22/.local/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [4]:
# from datasets import load_dataset

# dataset = load_dataset("zhengyun21/PMC-Patients")

# l = []
# for i in range(len(dataset['train'])):
#     if ('brain' in dataset['train'][i]['patient'] and 'MRI' in dataset['train'][i]['patient']):
#         l.append(i)

# tsl = []
# for i in range(1800,2000):
#     tsl.append(dataset['train'][l[i]]['patient'])

# l = []
# for i in range(len(tsl)):
#     t = split_into_sentences(tsl[i])
#     s = ""
#     for j in range(len(t)):
#         s += t[j]
#         if 'MRI' in t[j]:
#             break
#     l.append(s)
#     tsl[i] = s

In [5]:
from transformers import pipeline
from transformers import AutoTokenizer, AutoModelForTokenClassification
import string


tokenizer = AutoTokenizer.from_pretrained("d4data/biomedical-ner-all")
model = AutoModelForTokenClassification.from_pretrained("d4data/biomedical-ner-all")

pipe = pipeline("ner", model=model, tokenizer=tokenizer, aggregation_strategy="max") # pass device=0 if using gpu
labelled_data = []


for m in range(len(osl)):

    c = 0
    x = 0
    o = 0
    l1 = []
    for i in range(len(osl[m].split('.'))):
        t = (pipe(osl[m].split('.')[i]))
        for j in range(len(t)):
            if t[j]['entity_group'] != 'Age' and  t[j]['entity_group'] != 'Sex' and t[j]['entity_group'] != 'Sign_symptom' and t[j]['entity_group'] != 'Duration' and t[j]['entity_group'] != 'Biological_structure':
                c+=1
        # print(t)
        # print(c)
        if c == len(t):
            o = i
            
            x += 1
        else:
            l1.append(osl[m].split('.')[i])
        c = 0
    # if  print(pipe(osl[509].split('.')[i])) == []:
    
    # print(osl[m].split('.')[o])
    # print(x)
    # print(len(l1))
    length = 0
    s = ""
    for i in range(len(l1)):
        length += len(l1[i].split())
        s += l1[i]
        s += ". "
    osl[m] = s
    # print(length)
    # print(s)


# for m in range(len(tsl)):

#     c = 0
#     x = 0
#     o = 0
#     l1 = []
#     for i in range(len(tsl[m].split('.'))):
#         t = (pipe(tsl[m].split('.')[i]))
#         for j in range(len(t)):
#             if t[j]['entity_group'] != 'Age' and  t[j]['entity_group'] != 'Sex' and t[j]['entity_group'] != 'Sign_symptom' and t[j]['entity_group'] != 'Duration' and t[j]['entity_group'] != 'Biological_structure':
#                 c+=1
#         # print(t)
#         # print(c)
#         if c == len(t):
#             o = i
            
#             x += 1
#         else:
#             l1.append(tsl[m].split('.')[i])
#         c = 0
#     # if  print(pipe(osl[509].split('.')[i])) == []:
    
#     # print(osl[m].split('.')[o])
#     # print(x)
#     # print(len(l1))
#     length = 0
#     s = ""
#     for i in range(len(l1)):
#         length += len(l1[i].split())
#         s += l1[i]
#         s += ". "
#     tsl[m] = s
    # print(length)
    # print(s)

In [6]:
for i in range(len(osl) - 1, -1, -1):
    if len(osl[i].split()) > 1000:
        osl.pop(i)

In [7]:
len(osl)

1798

In [8]:
import re

def tokenize_sentence(sentence):
    # Tokenize the sentence and remove special characters
    return re.findall(r'\b[\w-]+\b', sentence.lower())

def tokenize_sentences(sentences):
    tokenized_sentences = []



    
    for sentence in sentences:
        # Tokenize each sentence
        tokens = tokenize_sentence(sentence)
        tokenized_sentences.append(tokens)
    return tokenized_sentences
# Tokenize the sentences
osl_tokenized = tokenize_sentences(osl)


import re

def tokenize_sentence(sentence):
    # Tokenize the sentence and remove special characters
    return re.findall(r'\b[\w-]+\b', sentence.lower())

def tokenize_sentences(sentences):
    tokenized_sentences = []
    for sentence in sentences:
        # Tokenize each sentence
        tokens = tokenize_sentence(sentence)
        tokenized_sentences.append(tokens)
    return tokenized_sentences
# Tokenize the sentences

print(osl_tokenized[0])
print(osl_tokenized[1])

['a', '24-year-old', 'healthy', 'woman', 'presented', 'with', 'difficulty', 'breathing', 'and', 'dissatisfaction', 'with', 'her', 'facial', 'appearance', 'she', 'had', 'a', 'history', 'of', 'childhood', 'trauma', 'resulting', 'in', 'nasal', 'septum', 'deviation', 'and', 'external', 'nasal', 'deformity', 'four', 'months', 'after', 'a', 'successful', 'and', 'uneventful', 'septorhinoplasty', 'she', 'presented', 'to', 'the', 'emergency', 'department', 'with', 'blunt', 'nasal', 'trauma', 'resulting', 'in', 'a', 'septal', 'hematoma', 'which', 'was', 'drained', 'successfully', 'the', 'patient', 'was', 'discharged', 'with', 'no', 'adverse', 'sequelae', 'nfour', 'months', 'later', 'the', 'patient', 'sustained', 'nasal', 'trauma', 'again', 'this', 'time', 'accompanied', 'by', 'clear', 'nasal', 'discharge', 'raising', 'suspicion', 'of', 'cerebrospinal', 'fluid', 'csf', 'leak', 'the', 'patient', 'was', 'discharged', 'after', 'managing', 'the', 'nasal', 'injury', 'as', 'the', 'ct', 'brain', 'showed

In [9]:
big_list = []
for i in range(len(osl_tokenized)):
    orig_str = ""
    for j in range(len(osl_tokenized[i])):
        orig_str = orig_str + osl_tokenized[i][j] + ' '
    big_list.append(orig_str)

for i in range(len(big_list)):
    big_list[i] = big_list[i].split()

big_list

[['a',
  '24-year-old',
  'healthy',
  'woman',
  'presented',
  'with',
  'difficulty',
  'breathing',
  'and',
  'dissatisfaction',
  'with',
  'her',
  'facial',
  'appearance',
  'she',
  'had',
  'a',
  'history',
  'of',
  'childhood',
  'trauma',
  'resulting',
  'in',
  'nasal',
  'septum',
  'deviation',
  'and',
  'external',
  'nasal',
  'deformity',
  'four',
  'months',
  'after',
  'a',
  'successful',
  'and',
  'uneventful',
  'septorhinoplasty',
  'she',
  'presented',
  'to',
  'the',
  'emergency',
  'department',
  'with',
  'blunt',
  'nasal',
  'trauma',
  'resulting',
  'in',
  'a',
  'septal',
  'hematoma',
  'which',
  'was',
  'drained',
  'successfully',
  'the',
  'patient',
  'was',
  'discharged',
  'with',
  'no',
  'adverse',
  'sequelae',
  'nfour',
  'months',
  'later',
  'the',
  'patient',
  'sustained',
  'nasal',
  'trauma',
  'again',
  'this',
  'time',
  'accompanied',
  'by',
  'clear',
  'nasal',
  'discharge',
  'raising',
  'suspicion',
  '

In [10]:
max_train_character = 0
c = 0
for i in range(len(osl_tokenized)):
    character_map_word = []
    for j in range(len(osl_tokenized[i])):
        character_map_character = []
        c += 1
        if (len(osl_tokenized[i][j]) > max_train_character):
            print(osl_tokenized[i][j])
            max_train_character = len(osl_tokenized[i][j])

max_train_word = 0
for i in range(len(osl_tokenized)):
   if len(osl_tokenized[i]) > max_train_word:
        max_train_word = len(osl_tokenized[i])
print(max_train_word)
print(c)

a
24-year-old
dissatisfaction
septorhinoplasty
diffusion-weighted
immunohistochemistry
thoracic-abdominal-pelvic
t2-weighted-fluid-attenuated
reverse-transcriptase-polymerase
gadolinium-diethylenetriaminepenta-acetic
806
314331


In [11]:
char_mapping = {'a': 0, 'b': 1, 'c': 2, 'd': 3, 'e': 4, 'f': 5, 'g': 6, 'h': 7, 'i': 8, 'j': 9, 'k': 10,
                'l': 11, 'm': 12, 'n': 13, 'o': 14, 'p': 15, 'q': 16, 'r': 17, 's': 18, 't': 19, 'u': 20,
                'v': 21, 'w': 22, 'x': 23, 'y': 24, 'z': 25, '-': 26, '.': 27,
                '0': 28, '1': 29, '2': 30, '3': 31, '4': 32, '5': 33, '6': 34, '7': 35, '8': 36, '9': 37, '<unknown>':38, '<pad>':39}
import torch
char_map_sentence = []
for i in range(len(osl_tokenized)):
    character_map_word = []
    for j in range(len(osl_tokenized[i])):
        character_map_character = []
        for k in range(len(osl_tokenized[i][j])):
            char = osl_tokenized[i][j][k]
            if char in char_mapping:
                character_map_character.append(char_mapping[char])
            else:
              
                character_map_character.append(char_mapping['<unknown>'])
        for k in range(max_train_character - len(osl_tokenized[i][j])):
            character_map_character.append(char_mapping['<pad>'])

        
        character_map_word.append(character_map_character)

    for j in range(max_train_word - len(osl_tokenized[i])):
        character_map_word.append([39, ]*max_train_character)
    char_map_sentence.append(character_map_word)
char_map_sentence = torch.tensor(char_map_sentence)

char_map_sentence.shape



torch.Size([1798, 806, 41])

In [12]:
import torch
import torch.nn as nn

# Define the Character Encoder model with BiLSTM
class CharacterEncoder(nn.Module):
    def __init__(self, input_size, hidden_size):
        super(CharacterEncoder, self).__init__()
        self.hidden_size = hidden_size
        self.char_lstm = nn.LSTM(input_size, hidden_size // 2, bidirectional=True, batch_first=True)

    def forward(self, char_embeddings):
        # Pass through BiLSTM
        lstm_out, _ = self.char_lstm(char_embeddings)
        # Concatenate the last timestep hidden states
        last_hidden_fwd = lstm_out[:, -1, :self.hidden_size // 2]
        last_hidden_bwd = lstm_out[:, 0, self.hidden_size // 2:]
        char_encoded = torch.cat((last_hidden_fwd, last_hidden_bwd), dim=1)
        return char_encoded

# Define parameters
input_size = max_train_character  # Size of character embedding
hidden_size = 64  # Size of hidden states in the BiLSTM

# Initialize the character encoder model
char_encoder = CharacterEncoder(input_size, hidden_size)

# Iterate through each sentence in char_map_sentence
encoded_sentences = []
for sentence in char_map_sentence:
    # Convert the sentence to a tensor
    sentence_tensor = torch.tensor(sentence, dtype=torch.float)  # Assuming the character embeddings are float
    # Pass the sentence tensor through the character encoder
    encoded_words = []
    for word_embeddings in sentence_tensor:
        
        
        word_embeddings = word_embeddings.view(1, -1, input_size)
        # Pass through the character encoder
        word_encoded = char_encoder(word_embeddings)
        encoded_words.append(word_encoded)
    # Stack the encoded words to form the encoded sentence
    encoded_sentence = torch.stack(encoded_words)
    encoded_sentences.append(encoded_sentence)

# Stack the encoded sentences to obtain the final encoded tensor
final_encoded_tensor = torch.stack(encoded_sentences, dim=2).squeeze(2)


/tmp/ipykernel_29077/1622573706.py:31: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  sentence_tensor = torch.tensor(sentence, dtype=torch.float)  # Assuming the character embeddings are float


In [18]:
final_encoded_tensor.shape

torch.Size([806, 1, 1798, 64])

In [13]:
final_encoded_tensor.shape
big_list = []
for i in range(len(osl_tokenized)):
    orig_str = ""
    for j in range(len(osl_tokenized[i])):
        orig_str = orig_str + osl_tokenized[i][j] + ' '
    big_list.append(orig_str)
big_list
big_list_test = []
# for i in range(len(tsl_tokenized)):
#     orig_str = ""
#     for j in range(len(tsl_tokenized[i])):
#         orig_str = orig_str + tsl_tokenized[i][j] + ' '
#     big_list_test.append(orig_str)
# big_list_test


In [14]:
vocab_train = []
for i in range(len(osl_tokenized)):
    for j in range(len(osl_tokenized[i])):
        if (osl_tokenized[i][j] not in vocab_train):
            vocab_train.append(osl_tokenized[i][j])

In [15]:
#FOR TRAINING -> THIS IS USED

from transformers import AutoTokenizer, AutoModel
import torch
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load BioBERT tokenizer and model
tokenizer = AutoTokenizer.from_pretrained("dmis-lab/biobert-v1.1")
model = AutoModel.from_pretrained("dmis-lab/biobert-v1.1").to(device)

# List of wordsfrom
word_list = vocab_train # Replace with your list of words

# Initialize list to store embeddings
word_embeddings = []

# Iterate through each word
for word in word_list:
    # Tokenize word

    tokens = tokenizer(word, return_tensors="pt").to(device)
    
    # Pass tokens through BioBERT model
    with torch.no_grad():
        outputs = model(**tokens)
    
    # Get embeddings for the first token (CLS token)
    embedding = outputs.last_hidden_state[0][0]  # Assuming you want to use the CLS token embedding
    
    # Append embedding to list
    word_embeddings.append(embedding)

# Convert list of embeddings to tensor
word_embeddings = torch.stack(word_embeddings).to(device)


In [16]:

import torch

sentence_embeddings = []
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# LET US FIND SENTENCE EMBEDDINGS
for i in range(len(osl_tokenized)):
    each_word_embeddings = []
    for j in range(len(osl_tokenized[i])):
        # Create tensor and then move it to device
        word_embedding_tensor = torch.tensor(word_embeddings[word_list.index(osl_tokenized[i][j])]).to(device)
        each_word_embeddings.append(word_embedding_tensor)
        
    for t in range(max_train_word - len(osl_tokenized[i])):  # pad
        each_word_embeddings.append(torch.zeros(768).to(device))
    sentence_embeddings.append(torch.stack(each_word_embeddings))
    
sentence_embeddings = torch.stack(sentence_embeddings)



/tmp/ipykernel_29077/2224079260.py:11: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  word_embedding_tensor = torch.tensor(word_embeddings[word_list.index(osl_tokenized[i][j])]).to(device)


In [19]:
print(final_encoded_tensor.shape)
final_encoded_tensor=final_encoded_tensor.squeeze(1).view(1798,806,64)
final_encoded_tensor.shape

torch.Size([806, 1, 1798, 64])


torch.Size([1798, 806, 64])

In [43]:
import torch
device = final_encoded_tensor.device
sentence_embeddings = sentence_embeddings.to(device)

# Concatenate along the last dimension (dimension 2)
input_to_word_encoder = torch.cat((final_encoded_tensor, sentence_embeddings), dim=2)

In [44]:
print(final_encoded_tensor.shape)
print(sentence_embeddings.shape)
print(input_to_word_encoder.shape)

torch.Size([1798, 806, 64])
torch.Size([1798, 806, 768])
torch.Size([1798, 806, 832])


In [ ]:
osl[0]

'A 24-year-old healthy woman presented with difficulty breathing and dissatisfaction with her facial appearance. She had a history of childhood trauma resulting in nasal septum deviation and external nasal deformity. Four months after a successful and uneventful septorhinoplasty, she presented to the emergency department with blunt nasal trauma resulting in a septal hematoma, which was drained successfully; the patient was discharged with no adverse sequelae. \\nFour months later, the patient sustained nasal trauma again, this time accompanied by clear nasal discharge, raising suspicion of cerebrospinal fluid (CSF) leak. The patient was discharged after managing the nasal injury, as the CT brain showed an intact cribriform plate with no evidence of a CSF leak. Ten days later, she presented at the emergency department with dizziness and an unstable gait. She also had complaints of paresthesia for the past two months, beginning in her right hand and progressing to the right shoulder, arm

In [22]:
import torch

# Assuming 'labelled_data' is a list of lists containing labels for each word in the dataset
labelled_data = []
dataset = big_list
for i, text in enumerate(dataset):
    
    dataset[i] = text
    list_entities = pipe(text)
    text_words = text.split()
    labels = [0] * len(text_words)

    for entity in list_entities:
        entity_word = entity['word']
        entity_group = entity['entity_group']

        # Check if the entity group is 'Sign_symptom' or 'Duration'
        if entity_group == 'Sign_symptom':
            entity_words = entity_word.split()
            for i in range(len(text_words)):
                if text_words[i:i + len(entity_words)] == entity_words:
                    for j in range(i, i + len(entity_words)):
                        labels[j] = 1
        elif entity_group == 'Duration':
            entity_words = entity_word.split()
            for i in range(len(text_words)):
                if text_words[i:i + len(entity_words)] == entity_words:
                    for j in range(i, i + len(entity_words)):
                        labels[j] = 3
        elif entity_group == 'Sex':
            entity_words = entity_word.split()
            for i in range(len(text_words)):
                if text_words[i:i + len(entity_words)] == entity_words:
                    for j in range(i, i + len(entity_words)):
                        labels[j] = 4
        elif entity_group == 'Biological_structure':
            entity_words = entity_word.split()
            for i in range(len(text_words)):
                if text_words[i:i + len(entity_words)] == entity_words:
                    for j in range(i, i + len(entity_words)):
                        labels[j] = 5

    # Convert 'labels' list to a tensor and move it to device
    labels_tensor = torch.tensor(labels).to(device)
    labelled_data.append(labels_tensor)

print(labelled_data)
import torch

labelled_continued_symptoms = []
'''
0
1 -> S-SYM
2 -> I-SYM
3 -> DURATION
4 -> SEX
'''

for i in range(len(labelled_data)):
    labelled_data[i] = labelled_data[i].tolist()  # Convert tensors to lists for manipulation

    for j in range(len(labelled_data[i]) - 1):
        if labelled_data[i][j] == 1 and labelled_data[i][j] == labelled_data[i][j + 1]:
            labelled_data[i][j + 1] = 2
        if labelled_data[i][j] == 2 and labelled_data[i][j + 1] == 1:
            labelled_data[i][j + 1] = 2
        if labelled_data[i][j] == 5 and labelled_data[i][j + 1] == 1:
            labelled_data[i][j + 1] = 1  
        if labelled_data[i][j] == 1 and labelled_data[i][j + 1] == 5:
            labelled_data[i][j + 1] = 1

    # Convert the modified list back to a tensor and move it to device
    labelled_continued_symptoms_tensor = torch.tensor(labelled_data[i]).to(device)
    labelled_continued_symptoms.append(labelled_continued_symptoms_tensor)

print(labelled_continued_symptoms)


[tensor([0, 0, 0, 4, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5,
        1, 1, 0, 5, 5, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 5, 0,
        0, 0, 0, 5, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 5,
        0, 0, 0, 0, 0, 0, 0, 5, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 5,
        0, 0, 0, 0, 5, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 3, 3, 0, 0, 0, 5, 5,
        0, 0, 0, 0, 5, 5, 5, 0, 5, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 5, 5, 0, 5, 5, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0,
        5, 5, 0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 5, 0, 5, 5, 0,
        1, 1, 0, 0, 5, 0, 5, 5, 0, 0, 5, 5, 5]), tensor([0, 0, 4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 0,
        1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 5, 5, 1, 0, 0, 0, 0, 0, 0, 5, 0, 0, 0, 0,
        0, 0, 1, 0, 0, 5, 0, 0, 0, 0, 1, 0, 5, 0, 0, 5, 0, 0, 0, 0, 0,

In [45]:
from torch.nn.utils.rnn import pad_sequence
padded_data = pad_sequence([torch.tensor(seq) for seq in labelled_data], batch_first=True)

#TENSOR REPRESENTATION OF LABELS
padded_data.shape


torch.Size([1798, 806])

In [ ]:

# import torch

# # Assuming 'labelled_data' is a list of lists containing labels for each word in the dataset
# test_labelled_data = []
# dataset = big_list_test
# for i, text in enumerate(dataset):
    
#     dataset[i] = text
#     list_entities = pipe(text)
#     text_words = text.split()
#     labels = [0] * len(text_words)

#     for entity in list_entities:
#         entity_word = entity['word']
#         entity_group = entity['entity_group']

#         # Check if the entity group is 'Sign_symptom' or 'Duration'
#         if entity_group == 'Sign_symptom':
#             entity_words = entity_word.split()
#             for i in range(len(text_words)):
#                 if text_words[i:i + len(entity_words)] == entity_words:
#                     for j in range(i, i + len(entity_words)):
#                         labels[j] = 1
#         elif entity_group == 'Duration':
#             entity_words = entity_word.split()
#             for i in range(len(text_words)):
#                 if text_words[i:i + len(entity_words)] == entity_words:
#                     for j in range(i, i + len(entity_words)):
#                         labels[j] = 3
#         elif entity_group == 'Sex':
#             entity_words = entity_word.split()
#             for i in range(len(text_words)):
#                 if text_words[i:i + len(entity_words)] == entity_words:
#                     for j in range(i, i + len(entity_words)):
#                         labels[j] = 4
#         elif entity_group == 'Biological_structure':
#             entity_words = entity_word.split()
#             for i in range(len(text_words)):
#                 if text_words[i:i + len(entity_words)] == entity_words:
#                     for j in range(i, i + len(entity_words)):
#                         labels[j] = 5

#     # Convert 'labels' list to a tensor and move it to device
#     labels_tensor = torch.tensor(labels).to(device)
#     test_labelled_data.append(labels_tensor)

# print(test_labelled_data)

# import torch

# test_labelled_continued_symptoms = []
# '''
# 0
# 1 -> S-SYM
# 2 -> I-SYM
# 3 -> DURATION
# 4 -> SEX
# '''

# for i in range(len(test_labelled_data)):
#     test_labelled_data[i] = test_labelled_data[i].tolist()  # Convert tensors to lists for manipulation

#     for j in range(len(test_labelled_data[i]) - 1):
#         if test_labelled_data[i][j] == 1 and test_labelled_data[i][j] == test_labelled_data[i][j + 1]:
#             test_labelled_data[i][j + 1] = 2
#         if test_labelled_data[i][j] == 2 and test_labelled_data[i][j + 1] == 1:
#             test_labelled_data[i][j + 1] = 2
#         if test_labelled_data[i][j] == 5 and test_labelled_data[i][j + 1] == 1:
#             test_labelled_data[i][j + 1] = 1  
#         if test_labelled_data[i][j] == 1 and test_labelled_data[i][j + 1] == 5:
#             test_labelled_data[i][j + 1] = 1

#     # Convert the modified list back to a tensor and move it to device
#     test_labelled_continued_symptoms_tensor = torch.tensor(test_labelled_data[i]).to(device)
#     test_labelled_continued_symptoms.append(test_labelled_continued_symptoms_tensor)

# print(test_labelled_continued_symptoms)

[tensor([0, 0, 0, 0, 0, 0, 0, 4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 5, 5, 0, 0, 0, 0, 0, 0, 0, 5, 0, 5, 0, 0, 0, 5, 0,
        5, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 0, 5, 1, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 0, 0, 5, 1, 0, 0, 0, 0, 0, 0, 5,
        0, 5, 1, 0, 0, 3, 3, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 0, 5, 1, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 5, 0, 5]), tensor([0, 0, 0, 4, 0, 0, 1, 0, 0, 0, 3, 3, 0, 3, 0, 0, 0, 3, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 3, 3, 0, 0, 0, 0, 0, 3, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 3, 3,
        3, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0,
        1, 0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 3, 3, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 0, 1, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0,
        0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0,
        0, 5, 5, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 5, 0, 0,

In [ ]:
# from torch.nn.utils.rnn import pad_sequence
# test_padded_data = pad_sequence([torch.tensor(seq) for seq in test_labelled_data], batch_first=True).to(device)

# #TENSOR REPRESENTATION OF LABELS
# test_padded_data.shape


torch.Size([200, 590])

In [46]:
print(input_to_word_encoder.shape)
print(padded_data.shape)

torch.Size([1798, 806, 832])
torch.Size([1798, 806])


In [47]:
import torch
import torch.nn as nn
import torch.optim as optim

class LSTMModel(nn.Module):
    def __init__(self, input_size, hidden_size, num_layers, dropout):
        super(LSTMModel, self).__init__()
        self.hidden_size = hidden_size
        self.num_layers = num_layers
        
        # LSTM layer
        self.lstm = nn.LSTM(input_size, hidden_size, num_layers=num_layers, 
                            batch_first=True, dropout=dropout)
        
    def forward(self, embeddings):
        # Pass embeddings through LSTM
        lstm_out, _ = self.lstm(embeddings)
        
        return lstm_out

class NERModel(nn.Module):
    def __init__(self, input_size, hidden_size, num_layers, num_labels):
        super(NERModel, self).__init__()
        self.lstm = LSTMModel(input_size, hidden_size, num_layers, 0.0)
        self.linear = nn.Linear(hidden_size, num_labels)

    def forward(self, x):
        lstm_output = self.lstm(x)
        embeddings = self.linear(lstm_output)
        return embeddings

# Example usage:
input_size = 832  # Dimension of concatenated word embeddings
hidden_size = 32  # Dimension of LSTM hidden state
num_layers = 1    # Number of LSTM layers
num_labels = 6    # Number of NER labels
num_sentences = 1798

# Initialize the model
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = NERModel(input_size, hidden_size, num_layers, num_labels).to(device)

# Define loss function and optimizer
criterion = nn.CrossEntropyLoss()  # Use CrossEntropyLoss for classification tasks
optimizer = optim.Adam(model.parameters(), lr=0.0025)

# Initialize the ReduceLROnPlateau scheduler
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(optimizer, 'min', patience=4, factor=0.45, verbose=True)

# Assuming placeholders for input_to_word_encoder and padded_data
# You need to replace these with your actual dataset loading mechanism


# Training loop
num_epochs = 170
for epoch in range(num_epochs):
    model.train()  # Set model to training mode
    total_loss = 0.0
    for i in range(num_sentences):
        optimizer.zero_grad()

        # Assumed placeholders for the input and target sequences
        input_sequence = input_to_word_encoder[i].unsqueeze(0).detach().to(device) 
        target_sequence = padded_data[i].to(device) 
        target_sequence = target_sequence[:input_sequence.size(1)].to(device) 
        output = model(input_sequence.squeeze(0))
    
        loss = criterion(output.squeeze(0), target_sequence)
        loss.backward()
        optimizer.step()

        total_loss += loss.item()

    epoch_loss = total_loss / num_sentences
    print(f'Epoch [{epoch + 1}/{num_epochs}], Loss: {epoch_loss:.4f}')
    
    # Step the scheduler based on the epoch loss
    scheduler.step(epoch_loss)


Epoch [1/170], Loss: 0.1207
Epoch [2/170], Loss: 0.0843
Epoch [3/170], Loss: 0.0782
Epoch [4/170], Loss: 0.0751
Epoch [5/170], Loss: 0.0725
Epoch [6/170], Loss: 0.0708
Epoch [7/170], Loss: 0.0696
Epoch [8/170], Loss: 0.0690
Epoch [9/170], Loss: 0.0687
Epoch [10/170], Loss: 0.0678
Epoch [11/170], Loss: 0.0672
Epoch [12/170], Loss: 0.0667
Epoch [13/170], Loss: 0.0661
Epoch [14/170], Loss: 0.0655
Epoch [15/170], Loss: 0.0650
Epoch [16/170], Loss: 0.0646
Epoch [17/170], Loss: 0.0642
Epoch [18/170], Loss: 0.0638
Epoch [19/170], Loss: 0.0634
Epoch [20/170], Loss: 0.0630
Epoch [21/170], Loss: 0.0627
Epoch [22/170], Loss: 0.0625
Epoch [23/170], Loss: 0.0622
Epoch [24/170], Loss: 0.0620
Epoch [25/170], Loss: 0.0618
Epoch [26/170], Loss: 0.0615
Epoch [27/170], Loss: 0.0613
Epoch [28/170], Loss: 0.0611
Epoch [29/170], Loss: 0.0609
Epoch [30/170], Loss: 0.0607
Epoch [31/170], Loss: 0.0605
Epoch [32/170], Loss: 0.0604
Epoch [33/170], Loss: 0.0603
Epoch [34/170], Loss: 0.0600
Epoch [35/170], Loss: 0

In [50]:
padded_data[1797]

tensor([0, 0, 4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 2, 2, 0, 0,
        0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 2, 2, 2, 0, 0, 0, 1, 0, 1,
        0, 0, 0, 0, 0, 3, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 2, 2,
        5, 5, 0, 0, 0, 0, 0, 0, 0, 0, 5, 0, 0, 1, 0, 0, 0, 1, 2, 0, 0, 0, 1, 2,
        2, 2, 0, 5, 0, 0, 5, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0,
        1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0,
        1, 2, 0, 1, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 5, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [61]:
# Initialize variables to track total non-zero labels and correctly predicted non-zero labels
total_non_zero_labels = 0
correct_non_zero_labels = 0
correct_0 = 0
total_0 = 0
correct_labels_one =0
total_labels_one =0
correct_labels_two =0
total_labels_two =0
correct_labels_three =0
total_labels_three =0
correct_labels_four =0
total_labels_four =0
correct_labels_five =0
total_labels_five =0
total_correct =0
total =0
# Loop through the test cases
for i in range(1300, 1400):
    # Prepare your test data
    input_sequence = input_to_word_encoder[i].unsqueeze(0).to(device)
    target_sequence = padded_data[i].to(device)

    # Set the model to evaluation mode
    model.eval()

    # Forward pass for testing
    with torch.no_grad():  # Ensure no gradients are computed
        output = model(input_sequence.squeeze(0))  # Forward pass

    # Get the predicted labels
    _, predicted_labels = torch.max(output.squeeze(0), dim=1)

    # Get the actual labels
    actual_labels = target_sequence.cpu().numpy()
    
    # Filter out zero labels
    for j in range(len(predicted_labels)):
        #print(len(actual_labels) == len(predicted_labels))
        if target_sequence[j]==predicted_labels[j]:
                total_correct += 1
        total += 1
        if target_sequence[j] != 0 and predicted_labels[j] == target_sequence[j]:
            correct_non_zero_labels+=1
        if target_sequence[j] != 0:
            total_non_zero_labels += 1 
        if target_sequence[j] == 0 and predicted_labels[j] == target_sequence[j]:
            correct_0+=1
        if target_sequence[j] == 0 :
            total_0+=1
        if target_sequence[j] == 1 and predicted_labels[j] == target_sequence[j]:
            correct_labels_one+=1
        if target_sequence[j] == 1:
            total_labels_one += 1 
        if target_sequence[j] == 2 and predicted_labels[j] == target_sequence[j]:
            correct_labels_two+=1
        if target_sequence[j] == 2:
            total_labels_two += 1 
        if target_sequence[j] == 3 and predicted_labels[j] == target_sequence[j]:
            correct_labels_three+=1
        if target_sequence[j] == 3:
            total_labels_three += 1 
        if target_sequence[j] == 4 and predicted_labels[j] == target_sequence[j]:
            correct_labels_four+=1
        if target_sequence[j] == 4:
            total_labels_four += 1 
        if target_sequence[j] == 5 and predicted_labels[j] == target_sequence[j]:
            correct_labels_five+=1
        if target_sequence[j] == 5:
            total_labels_five += 1 
# Calculate the accuracy of non-zero labels
non_zero_accuracy = correct_non_zero_labels / total_non_zero_labels
label_zero_accuracy = correct_0/total_0
label_one_accuracy = correct_labels_one/total_labels_one
label_two_accuracy = correct_labels_two/total_labels_two
label_four_accuracy = correct_labels_four/total_labels_four
label_three_accuracy = correct_labels_three/total_labels_three
label_five_accuracy = correct_labels_five/total_labels_five



# Print the accuracy of non-zero labels

print("Accuracy of label zero: ", label_zero_accuracy, "Ratio: ", correct_0,"/",total_0)
print("Accuracy of label one:", label_one_accuracy,"  Ratio: ", correct_labels_one,"/",total_labels_one)
print("Accuracy of label two:", label_two_accuracy, "  Ratio: ", correct_labels_two,"/",total_labels_two)
print("Accuracy of label three:", label_three_accuracy, "  Ratio: ", correct_labels_three,"/",total_labels_three)
print("Accuracy of label four:", label_four_accuracy, "  Ratio: ", correct_labels_four,"/",total_labels_four)
print("Accuracy of label five:", label_five_accuracy, "  Ratio: ", correct_labels_five,"/",total_labels_five)
print("Accuracy of non-zero labels:", non_zero_accuracy, "  Ratio: ", correct_non_zero_labels,"/",total_non_zero_labels )
print("NET ACCURACY: ", total_correct/total, "  Ratio: ", total_correct,"/",total)

Accuracy of label zero:  0.9925118508100224 Ratio:  76213 / 76788
Accuracy of label one: 0.6471418489767113   Ratio:  917 / 1417
Accuracy of label two: 0.6931982633863966   Ratio:  479 / 691
Accuracy of label three: 0.5827338129496403   Ratio:  162 / 278
Accuracy of label four: 0.9469026548672567   Ratio:  107 / 113
Accuracy of label five: 0.8758568164508759   Ratio:  1150 / 1313
Accuracy of non-zero labels: 0.7384575026232949   Ratio:  2815 / 3812
NET ACCURACY:  0.9804962779156328   Ratio:  79028 / 80600


In [ ]:
predicted_labels

tensor(0, device='cuda:0')

tensor([0, 0, 0, 0, 4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0,
        1, 0, 0, 0, 0, 0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 5, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 1, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,